## The Discourse API

As we move into more *real world examples*, it'll be nice to access, actual, live, large datasets. We've got a fun example coming up involving eigenvalues of a matrix generated by scraping data off of the web, in fact. For the time being, let's ease into data wrangling by interfacing with Discourse to see how we're doing there. First and foremost, Discourse is a website. It's a bit more than that, though, and you can interact with it quite fully via an API or Application Programming Interface. Check out the following two pages:

  * [https://discourse.marksmath.org/categories](https://discourse.marksmath.org/categories)
  * [https://discourse.marksmath.org/categories.json](https://discourse.marksmath.org/categories.json)

The first is just a pretty standard webpage on Discourse, though you might not have looked at it before. The second contains the same information, but formatted as [JSON](https://en.wikipedia.org/wiki/JSON). That highly structured format allows us to manipulate it with a computer quite easily. For example, here is a list of the publicly viewable categories currently on our Discourse, along with their `id`s.

In [1]:
import requests
response = requests.get("http://discourse.marksmath.org/categories.json")
response_json = response.json()
categories_with_ids=[(category['id'],category['name']) for category in response_json['category_list']['categories']]
categories_with_ids.sort()
categories_with_ids

[(1, 'Uncategorized'),
 (3, 'Site Feedback'),
 (5, 'Meta'),
 (6, 'Questions'),
 (7, 'Problems'),
 (8, 'Assignments'),
 (9, 'Ask and Answer'),
 (10, 'Quiz or test prep')]

There are a couple of things going on here. First, the [Requests Library](http://docs.python-requests.org/en/master/) (standard with Anaconda) is a great library for grabbing information off of the web. That's exactly what the requests.get() command did. Second, the response.json() command transformed the result into a Python dictionary, which JSON very closely resembles. In fact, we should probably take a quick look at JSON and Python dictionaries.

### JSON and Dictionaries

JSON (Javascript Object Notation) is a file format that is commonly used to transmit data between servers and browsers. Here's a sample:

    {
      "first_name": "Mark",
      "last_name": "McClure",
      "family": {
        "wife": "Adrienne",
        "kids": ["Audrey"],
        "Adrienne's kids": ["Adelaide", "Amelia"]
      },
      "favorite_letter": "A",
      "favorite_number": null
    }

I've got a file named `example.json` with exactly that content on my hard drive. Let's load it into Python using the `json` library - Python's standard tool for manipulating JSON:

In [2]:
import json
fp = open("example.json", "r")
json_in = json.load(fp)
fp.close()
json_in

{'first_name': 'Mark',
 'last_name': 'McClure',
 'family': {'wife': 'Adrienne',
  'kids': ['Audrey'],
  "Adrienne's kids": ['Adelaide', 'Amelia']},
 'favorite_letter': 'A',
 'favorite_number': None}

This result is a Python dictionary. Note that the syntax is very similar to the JSON we starte with, but not identical. It uses Python syntax and objects, rather than Javascript. The `null` in the orginal JSON, for example, appears as `None` in the resulting Python dictionary.

A dictionary is kind of like an array, but the elements are accessed by *key*, rather than by position. For example

In [3]:
json_in['first_name']

'Mark'

A more general term for this type of data structure is [associative array](https://en.wikipedia.org/wiki/Associative_array).

### Digging a little further

The inclusion of the category ids in our first data query allows us to form URLS to dig further into those categories. For example, here are all topics in the 'Quiz or test prep' category.

In [4]:
response = requests.get("http://discourse.marksmath.org/c/10.json")
response_json = response.json()
topic_titles = [topic['title'] for topic in response_json['topic_list']['topics']]
topic_titles

['About the Quiz or test prep category',
 'Applying the midpoint rule',
 'Symmetric difference quotient and data',
 'Deriving a difference quotient',
 'A least squares estimate',
 'A totally fictitious league',
 'A more realistic fiction',
 'Exponential least squares',
 'LogLoss',
 'A natural cubic spline',
 'A quadratic spline',
 'A Taylor approximation',
 'The IVT',
 'An interpolating polynomial',
 'A binary exansion',
 'Newton steps',
 'Bisection steps',
 'A floating point representation']

And here are all the topics in the 'Quiz or test prep' category that have been answered, together with their id and most recent poster.

In [5]:
topic_titles = [(topic['title'],topic['id'],topic['last_poster_username']) 
    for topic in response_json['topic_list']['topics'] if topic['posts_count'] > 1
]
topic_titles

[('Applying the midpoint rule', 72, 'Lorentz'),
 ('Symmetric difference quotient and data', 73, 'MatheMagician'),
 ('Deriving a difference quotient', 74, 'nathan'),
 ('A least squares estimate', 61, 'Lorentz'),
 ('A totally fictitious league', 56, 'mark'),
 ('A more realistic fiction', 57, 'Lorentz'),
 ('Exponential least squares', 62, 'anonymous_user'),
 ('LogLoss', 63, 'anonymous_user'),
 ('A natural cubic spline', 65, 'anonymous_user'),
 ('A quadratic spline', 58, 'anonymous_user'),
 ('A Taylor approximation', 40, 'mark'),
 ('The IVT', 45, 'funmanbobyjo'),
 ('An interpolating polynomial', 46, 'mark'),
 ('A binary exansion', 41, 'Cornelius'),
 ('Newton steps', 43, 'Cornelius'),
 ('Bisection steps', 44, 'mark'),
 ('A floating point representation', 42, 'Cornelius')]

Way to take all the good ones **Cornelius**! Well, at least someone named CestBeau had something else to say. Let's find out what!

In [6]:
response = requests.get("https://discourse.marksmath.org/t/41.json")
posts = response.json()['post_stream']['posts']
[post['cooked'] for post in posts if post['username'] == 'CestBeau']

['<p>Way to take all the good ones cornelius</p>']

### API keys

You can get your hands on a lot more info with an API key. For example, here are all the usernames in the class:

In [12]:
# Users and their trust levels.
api_key_string = "api_key=LONG_CRAZY_STRING&api_username=mark"
api_key_string = "api_key=0fbfa4df09e2f02d417e05c828d27e9414b8b39ff3dcf8a91d90ae60693de491&api_username=mark"
response = requests.get("https://discourse.marksmath.org/admin/users.json?" + api_key_string)
users_json = response.json()

score_data = [[user['username']] for user in users_json if not user['username'] in 
              ['mark', 'audrey', 'system', 'discobot']]
print(str(len(score_data)) + " students")
score_data

22 students


[['funmanbobyjo'],
 ['CeasarsRevenge'],
 ['bitchin_camero'],
 ['MatheMagician'],
 ['Spin'],
 ['Lorentz'],
 ['opernie'],
 ['Sampson'],
 ['Cornelius'],
 ['Aisling'],
 ['poster'],
 ['jorho85'],
 ['theoldernoah'],
 ['kp53'],
 ['pbahls'],
 ['dumptruckman'],
 ['nathan'],
 ['anonymous_user'],
 ['Bara223'],
 ['dakota'],
 ['brian'],
 ['CestBeau']]

And here are those users that have received a 'like' from me on your personalized function.

In [13]:
# Check the assigned topics.
# Gotta check that I gave it a like as well.
topics_to_check = [
    {'topic_number':19, 'points':5}, # Personalized function
    {'topic_number':52, 'points':5}, # Optimize
    {'topic_number':50, 'points':10}, # Eigenranking
    {'topic_number':67, 'points':10}, # Derivative
]
for topic_info in topics_to_check:
    topic_number = str(topic_info['topic_number'])
    response = requests.get("https://discourse.marksmath.org/t/" + topic_number + ".json")
    post_ids = response.json()['post_stream']['stream']

    posts = response.json()['post_stream']['posts']
    page_count = 1
    while len(posts) < len(post_ids):
        page_count = page_count + 1
        response = requests.get("https://discourse.marksmath.org/t/" + topic_number + ".json?page="+str(page_count))
        posts.extend(response.json()['post_stream']['posts'])
    
    #print(posts)
    participants = []
    for post in posts:
        id = post['id']
        likers_url = "https://discourse.marksmath.org/post_action_users.json?post_action_type_id=2"
        likers_url = likers_url + '&id=' + str(id)
        likers = requests.get(likers_url)
        liker_ids = [liker['id'] for liker in likers.json()['post_action_users']]
        if 1 in liker_ids:
            participant = post['username']
            if not participant in participants:
                participants.append(participant)
    for entry in score_data:
        if entry[0] in participants:
            entry.append(topic_info['points'])
        else:
            entry.append(0)
score_data

[['funmanbobyjo', 5, 5, 10, 10],
 ['CeasarsRevenge', 5, 0, 0, 0],
 ['bitchin_camero', 5, 0, 0, 0],
 ['MatheMagician', 5, 0, 0, 0],
 ['Spin', 5, 5, 0, 0],
 ['Lorentz', 5, 5, 10, 10],
 ['opernie', 5, 5, 10, 10],
 ['Sampson', 5, 5, 10, 10],
 ['Cornelius', 5, 5, 10, 0],
 ['Aisling', 5, 0, 10, 0],
 ['poster', 5, 5, 0, 0],
 ['jorho85', 5, 5, 10, 10],
 ['theoldernoah', 5, 5, 10, 10],
 ['kp53', 0, 0, 0, 0],
 ['pbahls', 5, 0, 0, 0],
 ['dumptruckman', 5, 5, 10, 10],
 ['nathan', 5, 5, 10, 10],
 ['anonymous_user', 5, 5, 10, 10],
 ['Bara223', 5, 0, 10, 0],
 ['dakota', 5, 5, 10, 10],
 ['brian', 5, 5, 10, 10],
 ['CestBeau', 5, 5, 10, 10]]

In [18]:
[(sd[0],sum(sd[1:])) for sd in score_data]

[('funmanbobyjo', 30),
 ('CeasarsRevenge', 5),
 ('bitchin_camero', 5),
 ('MatheMagician', 5),
 ('Spin', 10),
 ('Lorentz', 30),
 ('opernie', 30),
 ('Sampson', 30),
 ('Cornelius', 20),
 ('Aisling', 15),
 ('poster', 10),
 ('jorho85', 30),
 ('theoldernoah', 30),
 ('kp53', 0),
 ('pbahls', 5),
 ('dumptruckman', 30),
 ('nathan', 30),
 ('anonymous_user', 30),
 ('Bara223', 15),
 ('dakota', 30),
 ('brian', 30),
 ('CestBeau', 30)]

Unfortunately, I certainly cannot share my API key with you!!